In [1]:
import json

def clean_author_metadata(file_path):
    """
    清洗 author_metadata.json 中的 photo 字段，为不以 'https' 开头的值补充前缀 'https://huggingface.co/'。
    Args:
        file_path (str): 文件路径
    """
    with open(file_path, 'r', encoding='utf-8') as f:
        author_data = json.load(f)

    # 遍历所有作者信息并清洗 photo 字段
    for author, details in author_data.items():
        photo_url = details.get('photo', '')
        if not photo_url.startswith('https'):
            # 补充前缀
            author_data[author]['photo'] = f"https://huggingface.co{photo_url}"

    # 写入清洗后的数据回到文件中
    with open(file_path, 'w', encoding='utf-8') as f:
        json.dump(author_data, f, ensure_ascii=False, indent=4)
        print(f"Data cleaning complete. Updated data saved to {file_path}")

# 示例：指定 author_metadata.json 的路径
file_path = "author_metadata.json"
clean_author_metadata(file_path)


Data cleaning complete. Updated data saved to author_metadata.json


In [2]:
import json
import os

def clean_model_metadata(metadata_file, tree_file, output_file):
    """
    清洗 model_metadata.json，通过填补衍生模型缺失的 'pipeline_tag' 属性。

    Args:
        metadata_file (str): model_metadata.json 的路径。
        tree_file (str): model_tree_raw.json 的路径。
        output_file (str): 清洗后数据的保存路径。
    """

    # 检查文件是否存在
    if not os.path.exists(metadata_file):
        print(f"错误：文件 {metadata_file} 不存在。")
        return
    if not os.path.exists(tree_file):
        print(f"错误：文件 {tree_file} 不存在。")
        return

    # 加载 model_metadata.json
    with open(metadata_file, 'r', encoding='utf-8') as f:
        try:
            model_metadata = json.load(f)
            print(f"成功加载 {metadata_file}。")
        except json.JSONDecodeError as e:
            print(f"错误：无法解析 {metadata_file}。错误信息：{e}")
            return

    # 加载 model_tree_raw.json
    with open(tree_file, 'r', encoding='utf-8') as f:
        try:
            model_tree_raw = json.load(f)
            print(f"成功加载 {tree_file}。")
        except json.JSONDecodeError as e:
            print(f"错误：无法解析 {tree_file}。错误信息：{e}")
            return

    # 记录缺失 'pipeline_tag' 的衍生模型
    missing_pipeline_tags = []

    # 遍历每个基模型及其衍生模型
    for base_model, dependencies in model_tree_raw.items():
        # 获取基模型的 'pipeline_tag'，默认为 None
        base_pipeline_tag = model_metadata.get(base_model, {}).get('pipeline_tag')

        for dep_type, derived_models in dependencies.items():
            for derived_model in derived_models:
                # 检查衍生模型是否存在于 model_metadata.json 中
                if derived_model in model_metadata:
                    derived_pipeline_tag = model_metadata[derived_model].get('pipeline_tag')

                    if derived_pipeline_tag is None:
                        if base_pipeline_tag is not None:
                            # 填补衍生模型的 'pipeline_tag' 为基模型的值
                            model_metadata[derived_model]['pipeline_tag'] = base_pipeline_tag
                            print(f"更新模型 '{derived_model}' 的 'pipeline_tag' 为基模型 '{base_model}' 的值：'{base_pipeline_tag}'。")
                        else:
                            # 如果基模型的 'pipeline_tag' 也是 None，设置为 'nan'
                            model_metadata[derived_model]['pipeline_tag'] = 'nan'
                            missing_pipeline_tags.append(derived_model)
                            print(f"更新模型 '{derived_model}' 的 'pipeline_tag' 为 'nan'。")

    # 如果存在缺失 'pipeline_tag' 的模型，记录日志
    if missing_pipeline_tags:
        print("\n警告：以下衍生模型的 'pipeline_tag' 被设置为 'nan'，因为它们的基模型的 'pipeline_tag' 也是缺失的：")
        for model in missing_pipeline_tags:
            print(f"- {model}")

    # 保存清洗后的数据到新的 JSON 文件
    with open(output_file, 'w', encoding='utf-8') as f:
        json.dump(model_metadata, f, indent=4, ensure_ascii=False)
        print(f"\n清洗后的数据已保存到 {output_file}。")

    print("\n数据清洗完成。")

if __name__ == "__main__":
    # 定义文件路径
    metadata_file = 'model_metadata.json'
    tree_file = 'model_tree_raw.json'
    output_file = 'cleaned_model_metadata.json'

    # 调用清洗函数
    clean_model_metadata(metadata_file, tree_file, output_file)


成功加载 model_metadata.json。
成功加载 model_tree_raw.json。
更新模型 'Jonathanmann/Llama3.2-1B-SMS-All' 的 'pipeline_tag' 为基模型 'meta-llama/Llama-3.2-1B' 的值：'text-generation'。
更新模型 'doganmustafa/Llama-3.2-1B' 的 'pipeline_tag' 为基模型 'meta-llama/Llama-3.2-1B' 的值：'text-generation'。
更新模型 'Judiht/finetuned_Llama-3.2-1B_testcase_generator_1k' 的 'pipeline_tag' 为基模型 'meta-llama/Llama-3.2-1B' 的值：'text-generation'。
更新模型 'brightdatum/therapychatbot2' 的 'pipeline_tag' 为基模型 'meta-llama/Llama-3.2-1B' 的值：'text-generation'。
更新模型 'dhlim55/mental_health_happydb_llama' 的 'pipeline_tag' 为基模型 'meta-llama/Llama-3.2-1B' 的值：'text-generation'。
更新模型 'Pragades/llama3.1-mini-QLoRA' 的 'pipeline_tag' 为基模型 'meta-llama/Llama-3.2-1B' 的值：'text-generation'。
更新模型 'Peterhnn/finetuned_assignment_3.v1' 的 'pipeline_tag' 为基模型 'meta-llama/Llama-3.2-1B' 的值：'text-generation'。
更新模型 'brightdatum/therapychatbot' 的 'pipeline_tag' 为基模型 'meta-llama/Llama-3.2-1B' 的值：'text-generation'。
更新模型 'Jonathanmann/Llama3.2-1B-SMS-Young' 的 'pipeline_tag' 为基模型 'm